Extraccion y prueba de de datos

In [2]:


# -------Librerias -------#

import requests
import pandas as pd
import dateparser
import sys
import numpy as np


# ---- Como se compone la URL ---- #
# https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/[IdIndicador]/[Idioma]/[Área Geográfica]/[Recientes]/[Fuente de datos]/[Versión][Token]?type=[Formato]
'''
IdIndicador
El primer paso que se debe realizar para obtener información de la API es seleccionar el indicador e identificar su clave. Esto lo puede realizar consultando el "Constructor de consultas".

Idioma
La información está disponible en español [es] e inglés [en].

Área geográfica
Puede ser nacional [00], por entidad federativa [99] o por municipio [999], dependiendo de cada indicador.

Dato más reciente o Serie histórica
Puede consultarse solo el dato más reciente [true] o la serie histórica completa [false].

Fuente de datos
Corresponde a la fuente de diseminación [BISE] o [BIE] de donde se obtendrán los datos consultados.

Versión
Con él se identificará la edición [2.0] del servicio de provisión de datos.

Token
Para utilizar la API es necesario mandarle un token válido, el cual puede obtener al registrarse aquí.

Formato
Se ofrece la información en 3 tipos de formatos: JSON [json], JSONP [jsonp] o XML [xml].
'''


# Token personal del INEGI
TOKEN = 'ccf9a2b3-64b9-4eb8-f202-a8cd92076d04'

# Indicador del PIB nacional a precios constantes de 2018 (trimestral)
INDICADOR_PIB_CONST = 735879  # (Fuente INEGI BIE)

# Área gragrafica
ag = '0700'  # Nacional

# URL para obtener el indicador del PIB nacional a precios constantes
url = f'https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/{INDICADOR_PIB_CONST}/es/{ag}/false/BIE/2.0/{TOKEN}?type=json'

response = requests.get(url)
data = response.json()

# Extraer valores
valores = data['Series'][0]['OBSERVATIONS']

# Convertir a DataFrame
df_pib = pd.DataFrame(valores)

# Separar año y trimestre
df_pib[['anio', 'trimestre']] = df_pib['TIME_PERIOD'].str.split('/', expand=True)

# Mapear trimestres a fechas representativas
mes_inicio_trimestre = {
    '01': '01',  # Q1 → enero
    '02': '04',  # Q2 → abril
    '03': '07',  # Q3 → julio
    '04': '10'   # Q4 → octubre
}
# Crear columna de fecha válida
df_pib['fecha'] = pd.to_datetime(df_pib['anio'] + '-' + df_pib['trimestre'].map(mes_inicio_trimestre) + '-01')

# Dar Formato de valores númericos
df_pib['PIB_N'] = pd.to_numeric(df_pib['OBS_VALUE'], errors='coerce')
# Ordenar las fechas de mas antiguo al más reciente
df_pib = df_pib[['fecha', 'PIB_N']].sort_values('fecha')


# Extraer año desde la fecha
df_pib['anio'] = df_pib['fecha'].dt.year

# Agrupar por año y sumar PIB trimestral
df_pib_anual = df_pib.groupby('anio', as_index=False)['PIB_N'].sum()

# Mostrar resultado
df_pib_anual.rename(columns={'anio': 'date'}, inplace=True)
# df_pib_anual.to_csv("Data/pib_anual.csv", index=False)
df_pib_anual.tail()

date         PIB_N
41  2021  9.361932e+07
42  2022  9.709237e+07
43  2023  1.003484e+08
44  2024  1.017808e+08
45  2025  5.066242e+07

In [20]:
url_ace = f'  https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/481849/es/0700/true/BISE/2.0/{TOKEN}?type=json'
response = requests.get(url_ace)
data = response.json()
data
# # Extraer valores
# valores = data['Series'][0]['OBSERVATIONS']

# # Convertir a DataFrame
# df_pib = pd.DataFrame(valores)
# df_pib.head()

{'Header': {'Name': 'Datos compactos BISE',
  'Email': 'atencion.usuarios@inegi.org.mx'},
 'Series': [{'INDICADOR': '481849',
   'FREQ': '3',
   'TOPIC': '87',
   'UNIT': '977',
   'UNIT_MULT': '',
   'NOTE': '',
   'SOURCE': '12022',
   'LASTUPDATE': '19/10/2023 12:00:00 a. m.',
   'STATUS': None,
   'OBSERVATIONS': [{'TIME_PERIOD': '2021',
     'OBS_VALUE': '611866.50600000000000000000',
     'OBS_EXCEPTION': None,
     'OBS_STATUS': '1',
     'OBS_SOURCE': '',
     'OBS_NOTE': '',
     'COBER_GEO': '0700'}]}]}

In [4]:
# ---- Extracción de la tasa objetivo diaria del Banco de México ---- #

token_banxico = '3f1b778eb9764c78aebf314182c78d98f26cc66dfae50d4a5fc61a61f52015f6'

# ID de la serie de tasa objetivo diaria
serie_id = 'SF61745' 

url = f'https://www.banxico.org.mx/SieAPIRest/service/v1/series/{serie_id}/datos'


headers = {'Bmx-Token': token_banxico}

response = requests.get(url, headers=headers)

if response.status_code == 200:
    datos = response.json()
    observaciones = datos['bmx']['series'][0]['datos']
    
    df_tasa = pd.DataFrame(observaciones)
    df_tasa['fecha'] = pd.to_datetime(df_tasa['fecha'], dayfirst=True)
    df_tasa['Tasa objetivo diaria'] = pd.to_numeric(df_tasa['dato'], errors='coerce')
    df_tasa = df_tasa[['fecha', 'Tasa objetivo diaria']].sort_values('fecha')
    #display(df_tasa.tail())
else:
    print("Error en la consulta:", response.status_code)
    print(response.text[:500])


# Asegurarte de que la fecha sea el índice
df_tasa.set_index('fecha', inplace=True)

# Calcular promedio de tasa por trimestre (fin de trimestre)
df_trimestral_raw = df_tasa.resample('QE').mean()

# Reasignar ese promedio al primer día del siguiente trimestre
df_tasa_trimestral = df_trimestral_raw.copy()
df_tasa_trimestral.index = df_tasa_trimestral.index + pd.offsets.QuarterBegin(startingMonth=1)

# Resetear índice si lo necesitas como columna
df_tasa_trimestral = df_tasa_trimestral.reset_index()
df_tasa_trimestral.columns = ['fecha', 'tasa_referencia']


# Extraer año desde la fecha
df_tasa_trimestral['anio'] = df_tasa_trimestral['fecha'].dt.year

# Agrupar por año y calcular el promedio anual
df_tasa_anual = df_tasa_trimestral.groupby('anio', as_index=False)['tasa_referencia'].mean().round(2)

# Mostrar resultado
df_tasa_anual.rename(columns={"anio": "date"}, inplace=True)
# df_tasa_anual.to_csv("Data/tasa_referencia_anual.csv", index=False)
df_tasa_anual.tail()

date  tasa_referencia
13  2021             4.19
14  2022             6.44
15  2023            10.76
16  2024            11.08
17  2025             9.16

In [5]:
#URL para obtener el personas economicamente activas (PEA) a nivel nacional
url_empleo = f' https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/6200093960/es/0700/false/BISE/2.0/{TOKEN}?type=json'

response_empleo = requests.get(url_empleo)
data_empleo = response_empleo.json()

# Extraer valores
valores_empleo = data_empleo['Series'][0]['OBSERVATIONS']
# Convertir a DataFrame
df_empleo = pd.DataFrame(valores_empleo)
# Separar año y trimestre
df_empleo[['anio', 'trimestre']] = df_empleo['TIME_PERIOD'].str.split('/', expand=True)
# Crear columna de fecha válida
df_empleo['fecha'] = pd.to_datetime(df_empleo['anio'] + '-' + df_empleo['trimestre'].map(mes_inicio_trimestre) + '-01')
# Dar Formato de valores númericos
df_empleo['PEA'] = pd.to_numeric(df_empleo['OBS_VALUE'], errors='coerce')
# Ordenar las fechas de mas antiguo al más reciente
df_empleo = df_empleo[['fecha', 'PEA']].sort_values('fecha')


# URL para obtener el población desempleada a nivel nacional
url_desempleo = f'https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/6200093973/es/0700/false/BISE/2.0/{TOKEN}?type=json'

response_desempleo = requests.get(url_desempleo)
data_desempleo = response_desempleo.json()

# Extraer valores
valores_desempleo = data_desempleo['Series'][0]['OBSERVATIONS']
# Convertir a DataFrame
df_desempleo = pd.DataFrame(valores_desempleo)
# Separar año y trimestre
df_desempleo[['anio', 'trimestre']] = df_desempleo['TIME_PERIOD'].str.split('/', expand=True)
# Crear columna de fecha válida
df_desempleo['fecha'] = pd.to_datetime(df_desempleo['anio'] + '-' + df_desempleo['trimestre'].map(mes_inicio_trimestre) + '-01')
# Dar Formato de valores númericos
df_desempleo['valor'] = pd.to_numeric(df_desempleo['OBS_VALUE'], errors='coerce')
# Ordenar las fechas de mas antiguo al más reciente
df_desempleo = df_desempleo[['fecha', 'valor']].sort_values('fecha')

# Unir los DataFrames de empleo y desempleo
df_empleo['desempleo'] = df_desempleo['valor']

# Calcular la tasa de desempleo
df_empleo['tasa_desempleo'] = (df_empleo['desempleo'] / df_empleo['PEA']) * 100


# Extraer año desde la columna fecha
df_empleo['anio'] = df_empleo['fecha'].dt.year

# Agrupar por año y calcular promedios
df_empleo_anual = df_empleo.groupby('anio', as_index=False).agg({
    'PEA': 'mean',
    'desempleo': 'mean',
    'tasa_desempleo': 'mean'
}).round(2)

# Mostrar resultados
df_empleo_anual.rename(columns={"anio": "date"}, inplace=True)
# df_empleo_anual.to_csv("Data/empleo_desempleo_anual.csv", index=False)
df_empleo_anual.tail(5) # Mostrar los últimos 5 registros

date          PEA   desempleo  tasa_desempleo
16  2021  57530656.50  2364791.75            4.11
17  2022  59262415.00  1940016.50            3.28
18  2023  60585344.00  1688960.25            2.79
19  2024  61010596.25  1644631.00            2.69
20  2025  60778120.00  1557235.50            2.56

In [7]:

# Indicador INPC general base 2018 = 100
INDICADOR_INPC = 628258

# Área geográfica nacional
AG = "0700"

# Construir URL para el INPC
url = f'https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/{INDICADOR_INPC}/es/{AG}/false/BIE/2.0/{TOKEN}?type=json'

# Hacer la solicitud
response = requests.get(url)
data = response.json()

# Extraer observaciones
valores = data['Series'][0]['OBSERVATIONS']
df_inpc = pd.DataFrame(valores)

# Separar año y mes
df_inpc[['anio', 'mes']] = df_inpc['TIME_PERIOD'].str.split('/', expand=True)

# Crear columna de fecha
df_inpc['fecha'] = pd.to_datetime(df_inpc['anio'] + '-' + df_inpc['mes'] + '-01')

# Convertir valores a numérico
df_inpc['INPC'] = pd.to_numeric(df_inpc['OBS_VALUE'], errors='coerce')

# Limpiar columnas y ordenar
df_inpc = df_inpc[['fecha', 'INPC']].sort_values('fecha')

# Extraer año desde la fecha
df_inpc['anio'] = df_inpc['fecha'].dt.year

# Agrupar por año y calcular el promedio anual del INPC
df_inpc_anual = df_inpc.groupby('anio', as_index=False)['INPC'].mean().round(2)

# Mostrar resultado
df_inpc_anual.rename(columns={"anio": "date"}, inplace=True)
# df_inpc_anual.to_csv("Data/INPC_anual.csv", index=False)
df_inpc_anual


date  INPC
0  2018  2.91
1  2019  0.53
2  2020 -7.81
3  2021  4.50
4  2022  2.37
5  2023  4.19

In [9]:

INDICADOR_INFLACION_ANUAL = 628282  # Inflación anual INPC (%)
AG = "0700"  # Nacional


# Construir URL
url = (
    f"https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/"
    f"INDICATOR/{INDICADOR_INFLACION_ANUAL}/es/{AG}/false/BIE/2.0/{TOKEN}?type=json"
)

# Obtener respuesta
response = requests.get(url)
data = response.json()

# Extraer observaciones
valores = data['Series'][0]['OBSERVATIONS']
df_inflacion = pd.DataFrame(valores)

# Crear columnas de año y mes
df_inflacion[['anio', 'mes']] = df_inflacion['TIME_PERIOD'].str.split('/', expand=True)
df_inflacion['fecha'] = pd.to_datetime(df_inflacion['anio'])

# Convertir valor a numérico
df_inflacion['Inflacion'] = pd.to_numeric(df_inflacion['OBS_VALUE'], errors='coerce')

# Agrupar por año y calcular promedio
df_inflacion_agrupado = df_inflacion.groupby(df_inflacion['fecha'].dt.year).mean(numeric_only=True).reset_index()

# Crear columna de fecha tipo datetime (año como fecha)
df_inflacion_agrupado['date'] = pd.to_datetime(df_inflacion_agrupado['fecha'], format='%Y')

# Seleccionar columnas finales
df_inflacion_final = df_inflacion_agrupado[['date', 'Inflacion']].sort_values('date')

# # Exportar a CSV
# df_inflacion_final.to_csv("Data/Inflacion_anual.csv", index=False)

# Mostrar vista final
df_inflacion_final.tail(5)  # Mostrar los últimos 5 registros para verificar

date     Inflacion
26 2019-01-01  5.488078e+06
27 2020-01-01  5.374695e+06
28 2021-01-01  5.424703e+06
29 2022-01-01  5.552481e+06
30 2023-01-01  5.608003e+06

In [10]:

INDICADOR = 380003  # Índice estatal de precios de materiales
AG = "070025"       # Sinaloa
FUENTE = "BIE"

url = f"https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/{INDICADOR}/es/{AG}/false/{FUENTE}/2.0/{TOKEN}?type=json"

response = requests.get(url)
data = response.json()

if "Series" in data and data["Series"]:
    valores = data['Series'][0]['OBSERVATIONS']
    df = pd.DataFrame(valores)
    df[['anio', 'mes']] = df['TIME_PERIOD'].str.split('/', expand=True)
    df['fecha'] = pd.to_datetime(df['anio'] + '-' + df['mes'] + '-01')
    df['indice_materiales'] = pd.to_numeric(df['OBS_VALUE'], errors='coerce')
    df = df[['fecha', 'indice_materiales']].sort_values('fecha')
else:
    print("❌ No se encontraron datos:")
    print(data)

df.tail()


fecha  indice_materiales
4 2013-02-01               95.2
3 2013-03-01               98.7
2 2013-04-01              112.3
1 2014-01-01               94.1
0 2014-02-01               98.9

In [12]:

# Diccionario de nombres de estados (INEGI)
estados = {
    1: 'Aguascalientes', 2: 'Baja California', 3: 'Baja California Sur', 4: 'Campeche',
    5: 'Coahuila', 6: 'Colima', 7: 'Chiapas', 8: 'Chihuahua', 9: 'Ciudad de México',
    10: 'Durango', 11: 'Guanajuato', 12: 'Guerrero', 13: 'Hidalgo', 14: 'Jalisco',
    15: 'México', 16: 'Michoacán', 17: 'Morelos', 18: 'Nayarit', 19: 'Nuevo León',
    20: 'Oaxaca', 21: 'Puebla', 22: 'Querétaro', 23: 'Quintana Roo', 24: 'San Luis Potosí',
    25: 'Sinaloa', 26: 'Sonora', 27: 'Tabasco', 28: 'Tamaulipas', 29: 'Tlaxcala',
    30: 'Veracruz', 31: 'Yucatán', 32: 'Zacatecas'
}

# Mapeo de trimestre a mes
mes_inicio_trimestre = {'01': '01', '02': '04', '03': '07', '04': '10'}

# DataFrame total
df_total = pd.DataFrame()



# Iterar por estados
for i in range(1, 33):
    codigo_estado = str(i).zfill(2)
    geo_code = f'070000{codigo_estado}'

    url = f'https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/6207061361/es/{geo_code}/false/BISE/2.0/{TOKEN}?type=json'
    response = requests.get(url)

    if response.status_code != 200:
        print(f"Error al obtener datos del estado {codigo_estado} - {estados[i]}")
        continue

    try:
        data = response.json()
        observaciones = data['Series'][0]['OBSERVATIONS']
        df = pd.DataFrame(observaciones)

        df = df[df['TIME_PERIOD'].str.contains(r'^\d{4}/0[1-4]$')].copy()
        df[['anio', 'trimestre']] = df['TIME_PERIOD'].str.split('/', expand=True)
        df['mes'] = df['trimestre'].map(mes_inicio_trimestre)
        df = df[df['mes'].notna()]
        df['fecha'] = pd.to_datetime(df['anio'] + '-' + df['mes'] + '-01')
        df['ITAE'] = pd.to_numeric(df['OBS_VALUE'], errors='coerce')
        df['estado'] = estados[i]

        df_estado = df[['fecha', 'estado', 'ITAE']]
        df_total = pd.concat([df_total, df_estado], ignore_index=True)

    except Exception as e:
        print(f"❌ Error procesando {estados[i]}: {e}")

# Eliminar nulos
df_total = df_total.dropna()

# Pivotar para que cada estado sea columna
df_pivot = df_total.pivot(index="fecha", columns="estado", values="ITAE")

# Ordenar por fecha
df_pivot = df_pivot.sort_index()

# Asegurar que el índice sea datetime y extraer año
df_pivot = df_pivot.copy()
df_pivot['anio'] = df_pivot.index.year

# Agrupar por año y calcular el promedio anual por estado
df_itaee_anual = df_pivot.groupby('anio').mean().round(2)

# Resetear índice para tener 'anio' como columna
df_itaee_anual = df_itaee_anual.reset_index()

# Crear y guardar un CSV por cada columna (estado)
#for estado in df_itaee_anual.columns[1:]:
#    df_estado = df_itaee_anual[['anio', estado]].copy()
#    df_estado.columns = ['date', 'value']
#    filename = f"Data/Actividad_economica_{estado.replace(' ', '_')}.csv"
#    df_estado.to_csv(filename, index=False)
    
# Mostrar resultado
df_itaee_anual.rename(columns={"anio": "date"}, inplace=True)
# df_itaee_anual.to_csv('Data/Actividad_economica_ITAEE.csv')
df_itaee_anual

estado  date  Aguascalientes  Baja California  Baja California Sur  Campeche  \
0       2004            4.41             5.91                 7.16      1.15   
1       2005            2.50             2.39                 7.56     -1.97   
2       2006            6.51             5.30                 7.18     -2.34   
3       2007            8.93             1.25                13.38     -6.54   
4       2008            0.45            -0.79                 2.95     -8.46   
5       2009           -5.11           -10.83                -0.45     -9.98   
6       2010            6.34             4.97                 2.18     -3.39   
7       2011            4.42             2.96                 3.66     -3.64   
8       2012            5.56             3.48                 2.31     -1.58   
9       2013            3.06             2.10                -1.95      0.89   
10      2014           10.53             1.66                -0.10     -4.69   
11      2015            3.74             6.91                13.26     -7.06   
12      2016            7.26             3.68                 2.33     -5.83   
13      2017            3.56             3.30                12.33     -8.21   
14      2018            4.45             2.36                14.21     -1.26   
15      2019           -0.49             1.97                -7.31     -2.09   
16      2020           -7.17            -4.41               -21.18     -6.75   
17      2021            4.31             9.95                13.16     -3.51   
18      2022           -1.90             2.79                 8.23     -5.46   
19      2023            0.92             2.25                 8.54     -2.75   

estado  Chiapas  Chihuahua  Ciudad de México  Coahuila  Colima  ...  \
0         -3.87       4.56              4.40      2.91    0.14  ...   
1          0.81       3.31              1.39      2.14    0.69  ...   
2          3.45       7.80              5.21      4.77    6.31  ...   
3          1.71       3.59              1.40      4.13    6.94  ...   
4          2.36       1.46              1.68     -0.26    1.93  ...   
5         -0.58      -8.99             -3.49    -15.38   -3.17  ...   
6          5.59       4.18              3.65     16.44    7.22  ...   
7          3.17       2.24              3.55      6.87    7.38  ...   
8          1.90       7.53              3.96      5.07    2.94  ...   
9         -1.38       3.73              1.47     -2.05    0.99  ...   
10         5.23       2.22              2.16      5.13    2.53  ...   
11        -1.60       5.83              3.91      1.42    1.74  ...   
12        -2.01       5.12              4.64      1.88    4.37  ...   
13        -2.20       2.35              2.65      3.44    2.91  ...   
14        -0.50       0.99              2.63      0.94    1.45  ...   
15        -2.07       2.14             -0.18      1.08    4.29  ...   
16        -4.13      -5.92             -9.35    -10.91   -7.42  ...   
17         7.23       6.95              1.11      6.34    5.06  ...   
18         5.26       4.73              1.23      0.57    1.62  ...   
19         2.30       5.17              5.81      1.65   -0.06  ...   

estado  Quintana Roo  San Luis Potosí  Sinaloa  Sonora  Tabasco  Tamaulipas  \
0               8.82             5.87     6.13    5.22     4.36        4.75   
1               4.35             4.15     0.36    5.30     7.60        6.44   
2               6.98             4.63     3.21    6.20     5.84        3.03   
3              10.68             2.19     3.67    1.40     2.00        3.21   
4               5.24             2.21     3.59    0.30     4.64        4.21   
5              -8.42            -5.23    -4.29   -6.04     4.38       -8.95   
6               5.28             5.28     3.39    5.19     5.88        1.99   
7               5.61             5.39     2.05    9.27     4.72        1.92   
8               4.68             4.75     3.79    5.30     2.64        2.12   
9               4.43             3.57

In [51]:
path_csv = r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\Economics_data\Data\Producto-interno-bruto-trimestral-actividad-economica.csv"

In [53]:
import os
import time
import typing as T
import pandas as pd
import numpy as np
from dotenv import load_dotenv
import re
import json
import requests

def _fix_mojibake(text: str) -> str:
    """
    Si el CSV se leyó con el encoding incorrecto y trae 'Ã­' en vez de 'í',
    intentamos reparar con round-trip latin1->utf8. Si no hay error, devolvemos arreglado.
    """
    if not isinstance(text, str):
        return text
    try:
        # Si ya está bien, esto fallará y simplemente devolvemos el original
        repaired = text.encode("latin1").decode("utf-8")
        # Heurística: si al reparar aparecen caracteres con tildes válidos, usa repaired
        if "Ã" in text and ("á" in repaired or "é" in repaired or "í" in repaired or "ó" in repaired or "ú" in repaired or "ñ" in repaired):
            return repaired
    except Exception:
        pass
    return text

try:
    df = pd.read_csv(path_csv, encoding="utf-8-sig")
except UnicodeDecodeError:
    df = pd.read_csv(path_csv, encoding="latin-1")
df

Sector ID                                             Sector  Quarter ID  \
0           11  Agricultura, cría y explotación de animales, a...       19931   
1           11  Agricultura, cría y explotación de animales, a...       19932   
2           11  Agricultura, cría y explotación de animales, a...       19933   
3           11  Agricultura, cría y explotación de animales, a...       19934   
4           11  Agricultura, cría y explotación de animales, a...       19941   
...        ...                                                ...         ...   
2555        93  Actividades legislativas, gubernamentales, de ...       20234   
2556        93  Actividades legislativas, gubernamentales, de ...       20241   
2557        93  Actividades legislativas, gubernamentales, de ...       20242   
2558        93  Actividades legislativas, gubernamentales, de ...       20243   
2559        93  Actividades legislativas, gubernamentales, de ...       20244   

      Quarter            GDP           Time  
0     1993-T1    74640000000   728550000000  
1     1993-T2    78053000000   736239600000  
2     1993-T3    78360000000   744188400000  
3     1993-T4    85700000000   752137200000  
4     1994-T1    75729000000   760086000000  
...       ...            ...            ...  
2555  2023-T4  1161587000000  1698822000000  
2556  2024-T1  1090378000000  1706770800000  
2557  2024-T2  1136420000000  1714546800000  
2558  2024-T3  1152160000000  1722495600000  
2559  2024-T4  1214990000000  1730444400000  

[2560 rows x 6 columns]

In [46]:

# 2) Normalizar nombres de columnas
# Esperado en tu archivo: "Sector ID", "Sector", "Quarter ID", "Quarter", "GDP", "Time"
cols_map = {
    "Sector ID": "sector_id",
    "Sector": "sector",
    "Quarter ID": "quarter_id",
    "Quarter": "quarter",
    "GDP": "GDP",
    "Time": "Time",
}
# Si vienen con otras mayúsculas/espacios, hacemos un ajuste flexible
# df.columns = [c.strip() for c in df.columns]
for k, v in list(cols_map.items()):
    if k not in df.columns:
        # intenta localizar por lower/espacios
        match = [c for c in df.columns if c.lower().replace(" ", "") == k.lower().replace(" ", "")]
        if match:
            cols_map[k] = match[0]
# Renombra los que existan
df = df.rename(columns={cols_map.get(k, k): v for k, v in cols_map.items() if cols_map.get(k, k) in df.columns}).copy()
df

Sector ID                                             Sector  Quarter ID  \
0           11  Agricultura, cría y explotación de animales, a...       19931   
1           11  Agricultura, cría y explotación de animales, a...       19932   
2           11  Agricultura, cría y explotación de animales, a...       19933   
3           11  Agricultura, cría y explotación de animales, a...       19934   
4           11  Agricultura, cría y explotación de animales, a...       19941   
...        ...                                                ...         ...   
2555        93  Actividades legislativas, gubernamentales, de ...       20234   
2556        93  Actividades legislativas, gubernamentales, de ...       20241   
2557        93  Actividades legislativas, gubernamentales, de ...       20242   
2558        93  Actividades legislativas, gubernamentales, de ...       20243   
2559        93  Actividades legislativas, gubernamentales, de ...       20244   

      Quarter            GDP           Time  
0     1993-T1    74640000000   728550000000  
1     1993-T2    78053000000   736239600000  
2     1993-T3    78360000000   744188400000  
3     1993-T4    85700000000   752137200000  
4     1994-T1    75729000000   760086000000  
...       ...            ...            ...  
2555  2023-T4  1161587000000  1698822000000  
2556  2024-T1  1090378000000  1706770800000  
2557  2024-T2  1136420000000  1714546800000  
2558  2024-T3  1152160000000  1722495600000  
2559  2024-T4  1214990000000  1730444400000  

[2560 rows x 6 columns]

In [49]:

# 3) Repara mojibake en nombres de sector si hace falta
if "sector" in df.columns:
    df["sector"] = df["sector"].astype(str).map(_fix_mojibake)


# 5) Parsear Quarter a Period trimestral
# Quarter viene tipo "1993-T1", "2000-T4", etc.
def parse_quarter_to_period(q: str) -> pd.Period | None:
    if pd.isna(q):
        return None
    s = str(q).strip()
    m = re.search(r"(\d{4}).*?([1-4])", s)
    if not m:
        return None
    y, t = int(m.group(1)), int(m.group(2))
    return pd.Period(f"{y}Q{t}", freq="Q")

df["period"] = df.get("quarter", df.get("Quarter", None)).map(parse_quarter_to_period)
df = df.dropna(subset=["period"])

# 6) Convertir valores a float (soporta notación científica tipo '7.2855E+11' y enteros grandes)
def to_float(x):
    try:
        # Quita comas si las hubiera
        return float(str(x).replace(",", ""))
    except Exception:
        return np.nan

df["value"] = df['GDP'].map(to_float)
df = df.dropna(subset=["value"])
df

Sector ID                                             Sector  Quarter ID  \
0           11  Agricultura, cría y explotación de animales, a...       19931   
1           11  Agricultura, cría y explotación de animales, a...       19932   
2           11  Agricultura, cría y explotación de animales, a...       19933   
3           11  Agricultura, cría y explotación de animales, a...       19934   
4           11  Agricultura, cría y explotación de animales, a...       19941   
...        ...                                                ...         ...   
2555        93  Actividades legislativas, gubernamentales, de ...       20234   
2556        93  Actividades legislativas, gubernamentales, de ...       20241   
2557        93  Actividades legislativas, gubernamentales, de ...       20242   
2558        93  Actividades legislativas, gubernamentales, de ...       20243   
2559        93  Actividades legislativas, gubernamentales, de ...       20244   

      Quarter            GDP           Time  period         value  
0     1993-T1    74640000000   728550000000  1993Q1  7.464000e+10  
1     1993-T2    78053000000   736239600000  1993Q2  7.805300e+10  
2     1993-T3    78360000000   744188400000  1993Q3  7.836000e+10  
3     1993-T4    85700000000   752137200000  1993Q4  8.570000e+10  
4     1994-T1    75729000000   760086000000  1994Q1  7.572900e+10  
...       ...            ...            ...     ...           ...  
2555  2023-T4  1161587000000  1698822000000  2023Q4  1.161587e+12  
2556  2024-T1  1090378000000  1706770800000  2024Q1  1.090378e+12  
2557  2024-T2  1136420000000  1714546800000  2024Q2  1.136420e+12  
2558  2024-T3  1152160000000  1722495600000  2024Q3  1.152160e+12  
2559  2024-T4  1214990000000  1730444400000  2024Q4  1.214990e+12  

[2560 rows x 8 columns]

In [50]:
df['Quarter'].value_counts()

Quarter
1993-T1    20
1993-T2    20
1993-T3    20
1993-T4    20
1994-T1    20
           ..
2023-T4    20
2024-T1    20
2024-T2    20
2024-T3    20
2024-T4    20
Name: count, Length: 128, dtype: int64

In [48]:
last_q = df["period"].max()
last_q

Period('2024Q4', 'Q-DEC')

In [ ]:


# 7) Ordenar y generar auxiliares
#df = df.sort_values(["sector", "period"])
df["period_str"] = df["period"].astype(str).str.replace("Q", "T", regex=False)
df["date"] = df["period"].dt.to_timestamp(how="end")


In [40]:
df

Sector ID                                             Sector  Quarter ID  \
0           11  Agricultura, cría y explotación de animales, a...       19931   
1           11  Agricultura, cría y explotación de animales, a...       19932   
2           11  Agricultura, cría y explotación de animales, a...       19933   
3           11  Agricultura, cría y explotación de animales, a...       19934   
4           11  Agricultura, cría y explotación de animales, a...       19941   
...        ...                                                ...         ...   
2555        93  Actividades legislativas, gubernamentales, de ...       20234   
2556        93  Actividades legislativas, gubernamentales, de ...       20241   
2557        93  Actividades legislativas, gubernamentales, de ...       20242   
2558        93  Actividades legislativas, gubernamentales, de ...       20243   
2559        93  Actividades legislativas, gubernamentales, de ...       20244   

      Quarter            GDP           Time  period         value  
0     1993-T1    74640000000   728550000000  1993Q1  7.464000e+10  
1     1993-T2    78053000000   736239600000  1993Q2  7.805300e+10  
2     1993-T3    78360000000   744188400000  1993Q3  7.836000e+10  
3     1993-T4    85700000000   752137200000  1993Q4  8.570000e+10  
4     1994-T1    75729000000   760086000000  1994Q1  7.572900e+10  
...       ...            ...            ...     ...           ...  
2555  2023-T4  1161587000000  1698822000000  2023Q4  1.161587e+12  
2556  2024-T1  1090378000000  1706770800000  2024Q1  1.090378e+12  
2557  2024-T2  1136420000000  1714546800000  2024Q2  1.136420e+12  
2558  2024-T3  1152160000000  1722495600000  2024Q3  1.152160e+12  
2559  2024-T4  1214990000000  1730444400000  2024Q4  1.214990e+12  

[2560 rows x 8 columns]

In [ ]:


# 7) Ordenar y generar auxiliares
#df = df.sort_values(["sector", "period"])
df["period_str"] = df["period"].astype(str).str.replace("Q", "T", regex=False)
df["date"] = df["period"].dt.to_timestamp(how="end")

# 8) Devolver formato largo requerido y agregar por si hay duplicados
#out = (df.groupby(["sector", "period", "period_str", "date"], as_index=False)["value"].sum())
return df[["sector", "period", "period_str", "date", "value"]]


In [29]:
df_sect = load_gdp_by_sector_csv(path_csv, value_col="GDP")
df_sect.head(10)


KeyError: "['sector'] not in index"